<a href="https://colab.research.google.com/github/OlegKret/---/blob/master/Simplex_Big_M_Minimisation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [24]:
from fractions import Fraction

import numpy as np
from tabulate import tabulate




# Set NumPy print options to display fractions globally
np.set_printoptions(precision=3, suppress=True, linewidth=100,
                    formatter={'all': lambda x: str(Fraction(x).limit_denominator())})



def create_tableau_only_for_minimization(num_vars, objective_coeffs, num_constraints, constraint_coeffs, constraint_types, b_values):
    """
    Creates the initial tableau for the simplex method (minimization) with correct handling of artificial variables using Big M.
    """
    M = 1e6  # Big M value for artificial variables

    # Count the number of slack, surplus, and artificial variables
    num_slack_vars = sum(1 for t in constraint_types if t == '<=')
    num_surplus_vars = sum(1 for t in constraint_types if t == '>=')
    num_artificial_vars = sum(1 for t in constraint_types if t in ('>=', '='))

    total_columns = num_vars + num_slack_vars + num_surplus_vars + num_artificial_vars + 1  # +1 for RHS
    tableau = np.zeros((num_constraints + 1, total_columns), dtype=float)

    # List to track all variables (decision, slack, surplus, artificial)
    all_vars = [f'x{i+1}' for i in range(num_vars)]
    basis = []  # Basis stores the indices of basic variables

    # Fill the tableau with the constraints (Sequential placement)
    var_index = num_vars  # Start index for slack, surplus, and artificial variables
    for i in range(num_constraints):
        tableau[i, :num_vars] = constraint_coeffs[i]

        if constraint_types[i] == '<=':
            tableau[i, var_index] = 1  # Slack variable
            all_vars.append(f's{i + 1}')
            basis.append(var_index)  # Slack variables start in the basis
            var_index += 1

        elif constraint_types[i] == '>=':
            tableau[i, var_index] = -1  # Surplus variable
            all_vars.append(f'surplus{i + 1}')
            var_index += 1
            tableau[i, var_index] = 1  # Artificial variable
            all_vars.append(f'a{i + 1}')
            basis.append(var_index)  # Artificial variable starts in the basis
            var_index += 1

        elif constraint_types[i] == '=':
            tableau[i, var_index] = 1  # Artificial variable
            all_vars.append(f'a{i + 1}')
            basis.append(var_index)  # Artificial variable starts in the basis
            var_index += 1

        tableau[i, -1] = b_values[i]  # Fill RHS with b_values

    # Initialize the coefficients in the objective row
    coeffs = objective_coeffs[:]  # Copy the original objective function coefficients

    # Adjust for slack, surplus, and artificial variables
    for constraint_type in constraint_types:
        if constraint_type == '<=':
            coeffs.append(0)  # Slack variable coefficient = 0
        elif constraint_type == '>=':
            coeffs.append(0)  # Surplus variable coefficient = 0
            coeffs.append(M)  # Artificial variable coefficient = +M for minimization
        elif constraint_type == '=':
            coeffs.append(M)  # Artificial variable coefficient = +M for minimization

    # Calculate the objective row (reduced costs)
    for j in range(total_columns - 1):  # Exclude RHS column
        tableau[-1, j] = coeffs[j] - sum(coeffs[basis[i]] * tableau[i, j] for i in range(num_constraints))

    # Calculate RHS for the objective row
    # Multiply RHS values by the correct coefficient in the objective function (penalize artificial variables)
    tableau[-1, -1] = -sum(coeffs[basis[i]] * tableau[i, -1] for i in range(num_constraints))

    # Return the tableau and metadata
    tableau_metadata = {
        "all_vars": all_vars,  # List of all variable names (decision, slack, surplus, artificial)
        "basis": basis,        # Indices of the basic variables
        "coeffs": coeffs       # Coefficients from the objective function (with slack, surplus, and artificial)
    }

    return tableau, tableau_metadata




def identify_entering_column_minimization(tableau):
    """
    Identifies the entering column based on the objective row of the simplex tableau for minimization problems.

    Args:
        tableau: The current simplex tableau.

    Returns:
        entering_column: The index of the entering column, or None if the optimal solution has been reached.
    """
    # Extract the objective row (last row except for the RHS value)
    objective_row = tableau[-1, :-1]

    # Set a small tolerance to avoid floating-point precision issues
    tolerance = 1e-10

    # For minimization, select the most negative coefficient below tolerance
    min_value = np.min(objective_row)

    if min_value >= -tolerance:
        return None  # No sufficiently negative coefficient found, optimal solution reached

    # Select the index of the most negative coefficient
    entering_column = np.argmin(objective_row)

    # Print the entering column index and the most negative value
    print(f"Entering column index: {entering_column}")
    print(f"Most negative value in objective row: {min_value}")

    return entering_column




def identify_leaving_row_minimization(tableau, entering_column):
    """
    Identifies the leaving row based on the minimum ratio test in the simplex tableau for minimization problems.

    Args:
        tableau: The current simplex tableau.
        entering_column: The index of the entering column.

    Returns:
        leaving_row: The index of the leaving row, or None if the solution is unbounded.
    """
    num_rows = tableau.shape[0] - 1  # Exclude the objective row
    min_ratio = np.inf
    leaving_row = None

    # Perform the minimum ratio test
    for i in range(num_rows):
        rhs_value = tableau[i, -1]  # The RHS value for the current row
        entering_value = tableau[i, entering_column]  # Coefficient of the entering variable in this row

        # Only consider positive entering values to avoid division by zero or negative ratios
        if entering_value > 0:
            ratio = rhs_value / entering_value

            # Print the ratio for debugging purposes
            print(f"Row {i}: RHS = {rhs_value}, Entering Value = {entering_value}, Ratio = {ratio}")

            # Compare ratios, consider floating-point precision
            if ratio < min_ratio - 1e-10:
                min_ratio = ratio
                leaving_row = i
            elif abs(ratio - min_ratio) < 1e-10:
                # Optional: tie-breaking in case of degeneracy (first encountered row)
                if leaving_row is None or i < leaving_row:
                    leaving_row = i

    # Print the identified leaving row for debugging
    if leaving_row is not None:
        print(f"Identified leaving row: {leaving_row} with minimum ratio: {min_ratio}")
    else:
        print("No valid leaving row found, solution might be unbounded.")

    # If no valid leaving row is found, return None to indicate unbounded solution
    return leaving_row



def locate_pivot_element_minimization(tableau, entering_column, leaving_row):
    """
    Locates the pivot element in the simplex tableau for minimization problems.

    Args:
        tableau: The current simplex tableau.
        entering_column: The index of the entering column.
        leaving_row: The index of the leaving row.

    Returns:
        pivot_element: The value of the pivot element, or None if the leaving row is invalid.
    """
    if leaving_row is None:
        return None  # No valid pivot if no leaving row exists

    pivot_element = tableau[leaving_row, entering_column]

    # Ensure the pivot element is not zero (which would cause issues in row operations)
    if np.isclose(pivot_element, 0):
        raise ValueError(
            "Pivot element is zero indicating potential degeneracy or an error in selecting the pivot.")

    return pivot_element



def update_key_row_minimization(tableau, key_row, pivot_element):
    """
    Updates the key row in the simplex tableau for minimization problems.

    Args:
        tableau: The current simplex tableau.
        key_row: The index of the key (pivot) row.
        pivot_element: The pivot element in the tableau.

    Returns:
        tableau: The updated simplex tableau after normalizing the key row.
    """
    # Normalize the key row by dividing every element in the row by the pivot element
    tableau[key_row, :] /= pivot_element
    return tableau




def update_non_key_rows_minimization(tableau, entering_column, key_row):
    """
    Updates all non-key rows in the simplex tableau during minimization problems.

    Args:
        tableau: The current simplex tableau.
        entering_column: The index of the entering column.
        key_row: The index of the key (pivot) row.

    Returns:
        tableau: The updated simplex tableau after eliminating the entering variable from all non-key rows.
    """
    num_rows = tableau.shape[0]

    # Loop through each row and update all non-key rows
    for row in range(num_rows):
        if row != key_row:  # Skip the key row
            key_ratio = tableau[row, entering_column]  # Calculate the key ratio for this non-key row
            tableau[row, :] -= key_ratio * tableau[key_row, :]  # Eliminate the entering variable in this row

    return tableau




def update_objective_row_minimization(tableau, coeffs, basis, artificial_vars, all_vars):
    """
    Update the objective row in the tableau for minimization problems.
    """
    objective_row = tableau[-1, :]
    num_columns = len(objective_row) - 1  # Exclude the RHS column
    num_basis = len(basis)

    # Update the objective row for each column (except the RHS)
    for j in range(num_columns):
        original_coeff = coeffs[j]
        weighted_sum = sum(coeffs[basis[i]] * tableau[i, j] for i in range(num_basis))
        objective_row[j] = original_coeff - weighted_sum

    # Now update the RHS (optimal value) of the objective row
    optimal_value = sum(coeffs[basis[i]] * tableau[i, -1] for i in range(num_basis))
    objective_row[-1] = optimal_value







def update_artificial_vars_minimization(tableau, tableau_metadata, leaving_var_idx, artificial_vars, all_vars):
    """
    Zero out artificial variable columns and remove their contribution to the objective row when they leave the basis.

    Args:
    - tableau: The current simplex tableau.
    - tableau_metadata: Metadata related to the tableau (coefficients, variables, basis, etc.).
    - leaving_var_idx: Index of the variable that is leaving the basis.
    - artificial_vars: List of indices of artificial variables.
    - all_vars: List of all variable names (decision, slack, surplus, artificial).
    """
    if leaving_var_idx in artificial_vars:
        # Zero out the column corresponding to the artificial variable
        tableau[:, leaving_var_idx] = 0

        # Set the artificial variable's coefficient in the objective row to 0
        tableau_metadata["coeffs"][leaving_var_idx] = 0

        # Do not zero out any corresponding surplus variables
        surplus_var_name = all_vars[leaving_var_idx].replace("a", "surplus")
        if surplus_var_name in all_vars:
            surplus_var_idx = all_vars.index(surplus_var_name)
            # Ensure the surplus variable is unaffected
            if surplus_var_idx not in artificial_vars:
                tableau[:, surplus_var_idx] = tableau[:, surplus_var_idx]




def print_tableau_minimization(tableau, all_vars, basis, coeffs, constraint_types):
    """
    Prints the tableau with a header row, formatted output, and fractions.
    (Modified to include basis variable values in the BASIS column for minimization problems)

    Args:
        tableau: The current simplex tableau.
        all_vars: List of all variable names (decision, slack, surplus, artificial).
        basis: List of indices of the basic variables.
        coeffs: List of objective function coefficients for all variables.
        constraint_types: List of the constraint types for each row.
    """
    # Convert tableau elements to fractions for readability
    tableau_fractions = [[Fraction(x).limit_denominator() for x in row] for row in tableau]

    # Convert fractions to strings for tabulate
    tableau_strings = [[str(frac) for frac in row] for row in tableau_fractions]

    # Create the header row
    headers = ["Constraint Type", "BASIS"] + all_vars + ["RHS"]

    # Create the basis indicator row (BASIS row) - Corrected
    basis_indicator = ["BASIS"]
    for i in range(len(tableau) - 1):  # Go through each row except the objective row
        if i < len(basis):
            basis_var_index = basis[i]
            value = coeffs[basis_var_index]  # Get the coefficient from coeffs list
            basis_indicator.append(f"{all_vars[basis_var_index]} = {value}")
        else:
            basis_indicator.append("")  # Leave empty for non-basic rows
    basis_indicator += [""] * (len(headers) - len(basis_indicator))

    # Add the coefficient (objective function) row
    coeff_row = ["Coeff"] + [f"{Fraction(c).limit_denominator()}" for c in coeffs] + [""]

    # Combine rows with constraint types
    tableau_rows = []
    for i in range(len(tableau_strings) - 1):  # Skip the objective row
        row = [constraint_types[i], f"{all_vars[basis[i]]}"] + tableau_strings[i] + [str(tableau[i][-1])]
        tableau_rows.append(row)

    # Add the minimization objective function row (last row in the tableau)
    objective_row = ["Minimize", ""] + tableau_strings[-1] + [str(tableau[-1][-1])]

    # Add constraint types to the first column of each row
    for i in range(len(tableau_rows)):
        tableau_rows[i][0] = constraint_types[i]

    # Combine all rows for printing
    output_rows = []
    output_rows.append(basis_indicator)
    output_rows.append(coeff_row)
    output_rows.extend(tableau_rows)
    output_rows.append(objective_row)

    # Print the tableau using tabulate
    print(tabulate(output_rows, headers=headers, tablefmt="fancy_grid"))





def print_problem_summary_minimization(objective_function, constraints, all_vars, tableau, basis):
    """
    Prints a summary of the linear programming minimization problem with nicer formatting,
    including slack/surplus/artificial variables in the constraints, and shows the final
    objective function with the values of the basic variables.

    Args:
        objective_function: Coefficients of the objective function.
        constraints: List of constraints, each containing 'coeffs', 'type', and 'rhs'.
        all_vars: List of all variables (decision, slack, surplus, artificial).
        tableau: The final simplex tableau.
        basis: List of indices of the basic variables.
    """

    # Print objective function header
    print("Objective Function:")
    obj_str = "Minimize Z = "
    objective_terms = []

    # Build the objective function string with variable values from the tableau
    for i, var_idx in enumerate(basis):
        coef = objective_function[var_idx]
        if coef != 0:
            var_value = tableau[i, -1]  # Get the value from the tableau
            objective_terms.append(f"{coef}*{all_vars[var_idx]} = {coef * var_value}")

    # Add artificial variable terms (if any) for minimization with Big M
    artificial_terms = []
    for var_idx in range(len(all_vars)):
        if all_vars[var_idx].startswith('a'):
            coef = 1e6  # Big M is positive for minimization
            var_value = tableau[basis.index(var_idx), -1] if var_idx in basis else 0
            artificial_terms.append(f"{coef}*{all_vars[var_idx]} = {coef * var_value}")

    # Combine the objective function and artificial terms
    obj_str += " + ".join(objective_terms + artificial_terms)
    print(obj_str)

    # Print constraints
    print("\nConstraints:")
    for i, constraint in enumerate(constraints):  # Access constraints from the argument
        # Build the constraint string with coefficients and variables
        constraint_str = " + ".join(
            f"{Fraction(constraint['coeffs'][j]).limit_denominator()}*{all_vars[j]}"
            for j in range(len(constraint['coeffs']))
        )
        # Add slack, surplus, or artificial variable depending on the constraint type
        constraint_str += {
            "<=": f" + s{i + 1}",
            ">=": f" - surplus{i + 1} + a{i + 1}",
            "=": f" + a{i + 1}",
        }[constraint['type']]
        # Add the right-hand side of the constraint
        constraint_str += f" = {Fraction(constraint['rhs']).limit_denominator()}"
        print(f"{i + 1}. {constraint_str}")




def extract_solution_minimization(tableau_metadata):
    """
    Extracts the solution from the final simplex tableau for a minimization problem.

    Args:
        tableau_metadata: A dictionary containing the tableau, basis, all_vars, and other related information.

    Returns:
        solution: A dictionary containing the optimal solution or status of the problem.
    """
    tableau = tableau_metadata['tableau']
    basis = tableau_metadata['basis']
    all_vars = tableau_metadata['all_vars']
    artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

    # Check for artificial variables in the basis
    artificial_in_basis = any(basis_var in artificial_vars for basis_var in basis)
    if artificial_in_basis:
        return {"status": "infeasible", "message": "Artificial variable still in the basis, problem is infeasible."}

    # Extract variable values (including non-basic variables)
    variable_values = {}
    for i, var_name in enumerate(all_vars):
        if i in basis:
            row = basis.index(i)
            variable_values[var_name] = Fraction(tableau[row, -1]).limit_denominator()
        else:
            variable_values[var_name] = 0  # Non-basic variables have value 0

    # Calculate the optimal objective function value for minimization
    objective_value = Fraction(tableau[-1, -1]).limit_denominator()

    # Prepare the solution dictionary
    solution = {
        "status": "optimal",
        "objective_value": objective_value,  # The optimal value of the objective function
        "variable_values": variable_values  # The values of decision variables, slack, surplus, and artificial
    }

    return solution





def update_tableau_for_basis_change_minimization(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars):
    """
    Updates the basis and tableau when an entering variable replaces a leaving variable in a minimization problem.

    Args:
        tableau: The current simplex tableau.
        tableau_metadata: A dictionary containing tableau metadata (coefficients, variables, basis, etc.).
        entering_column: The index of the entering column.
        leaving_row: The index of the leaving row.
        artificial_vars: List of indices of artificial variables.
        all_vars: List of all variable names (decision, slack, surplus, artificial).
    """

    # Handle the basis change: Replace the leaving variable with the entering variable
    leaving_var_idx = tableau_metadata["basis"][leaving_row]
    tableau_metadata["basis"][leaving_row] = entering_column
    new_basis = tableau_metadata["basis"]

    # Zero out artificial variables when they leave the basis
    if leaving_var_idx in artificial_vars:
        tableau[:, leaving_var_idx] = 0  # Zero out the column corresponding to the artificial variable
        tableau_metadata["coeffs"][leaving_var_idx] = 0  # Set the coefficient to zero to remove the variable's contribution

    # Ensure that artificial variables do not re-enter the basis once they leave
    if entering_column in artificial_vars:
        tableau[:, entering_column] = 0  # Zero out the artificial variable's column
        tableau_metadata["coeffs"][entering_column] = 0  # Set the coefficient of the artificial variable to zero

    # Update the objective row after the basis change
    update_objective_row_minimization(tableau, tableau_metadata["coeffs"], new_basis, artificial_vars, all_vars)





def check_penalty_and_feasibility_minimization(tableau, all_vars, artificial_vars, M, tableau_metadata):
    """
    Check the final tableau for artificial variables and calculate the penalty for minimization problems.

    Args:
        tableau: The final simplex tableau.
        all_vars: The list of all variable names.
        artificial_vars: List of indices of artificial variables.
        M: The large penalty value used in the Big M method for minimization.
        tableau_metadata: A dictionary containing the tableau, basis, and other related information.

    Returns:
        penalty_m_term: The accumulated coefficient of M in the objective function.
        constant_value: The constant part of the objective value (RHS).
        feasible: True if no artificial variables remain in the basis, False if they do.
    """
    penalty_m_term = 0  # Represents the M-term coefficient for artificial variables
    constant_value = tableau[-1, -1]  # Start with the constant from the RHS of the objective row
    feasible = True  # Assume the solution is feasible unless proven otherwise

    # Debugging: Print artificial variables and their values
    print("\nChecking for artificial variables in the basis:")

    # Iterate over all artificial variables to check if they are still in the basis
    for i in artificial_vars:
        if i in tableau_metadata["basis"]:
            # If an artificial variable is still in the basis, it contributes to the penalty
            row_idx = tableau_metadata["basis"].index(i)
            value_in_basis = tableau[row_idx, -1]

            # Print debug information about the artificial variable and its value
            print(f"Artificial variable {all_vars[i]} is in the basis with value {value_in_basis}.")

            # For minimization, the penalty applies if the artificial variable has a positive value
            if value_in_basis > 0:
                penalty_m_term += value_in_basis  # Accumulate the penalty (positive value * M)
                feasible = False  # The solution is not feasible if artificial variables remain

    # Correct the objective value by adding the penalty (for minimization, we use +M)
    if not feasible:
        print(f"Penalty term due to artificial variables: {penalty_m_term} * M")
        constant_value += penalty_m_term * M  # Add the penalty term to the constant part of the objective value
        return penalty_m_term, constant_value, False  # Return the penalty, constant value, and infeasibility flag
    else:
        return 0, constant_value, True  # No penalty, solution is feasible






def update_basis_with_values(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars):
    """
    Updates the basis after performing a pivot, replacing the leaving variable with the entering variable
    and updating the value.
    """
    # Identify the leaving variable's index in the basis
    leaving_var_idx = tableau_metadata["basis"][leaving_row]

    # Replace the leaving variable with the entering variable
    tableau_metadata["basis"][leaving_row] = entering_column

    # If the leaving variable is artificial, zero out its column and set its coefficient to 0
    if leaving_var_idx in artificial_vars:
        tableau[:, leaving_var_idx] = 0
        tableau_metadata["coeffs"][leaving_var_idx] = 0  # Ensure the coefficient is zeroed out

    # Ensure that the artificial variable never re-enters the basis once it leaves
    if entering_column in artificial_vars:
        tableau[:, entering_column] = 0  # Zero out the artificial variable's column
        tableau_metadata["coeffs"][entering_column] = 0  # Set the artificial variable's coefficient to zero

    # Debugging: Print when an artificial variable leaves the basis
    if leaving_var_idx in artificial_vars:
        print(f"Artificial variable {all_vars[leaving_var_idx]} has left the basis.")

    # Update the objective row and other rows based on the new basis
    update_objective_row_minimization(tableau, tableau_metadata["coeffs"], tableau_metadata["basis"], artificial_vars, all_vars)




def check_constraint_violations(solution, constraint_coeffs, constraint_types, b_values):
    """
    Checks for constraint violations by comparing LHS and RHS values for each constraint.

    Args:
        solution: The current solution values for the variables.
        constraint_coeffs: List of coefficients for each constraint.
        constraint_types: List of constraint types ('<=', '>=', '=').
        b_values: List of RHS values for each constraint.

    Returns:
        A list of violations. Each violation is represented by a tuple (index, LHS value, RHS value, constraint type).
    """
    violations = []

    # Ensure the constraints lists have matching lengths
    num_constraints = min(len(constraint_coeffs), len(constraint_types), len(b_values))

    for i in range(num_constraints):
        coeffs = constraint_coeffs[i]
        lhs_value = sum(coeffs[j] * solution[f"x{j+1}"] for j in range(len(solution)))
        rhs_value = b_values[i]

        # Check based on constraint type
        if constraint_types[i] == '<=' and lhs_value > rhs_value:
            violations.append((i, lhs_value, rhs_value, '<='))
        elif constraint_types[i] == '>=' and lhs_value < rhs_value:
            violations.append((i, lhs_value, rhs_value, '>='))
        elif constraint_types[i] == '=' and lhs_value != rhs_value:
            violations.append((i, lhs_value, rhs_value, '='))

    return violations




def print_violation_report(violations, all_vars, constraint_coeffs):
    """
    Prints a report of the constraint violations.

    Args:
        violations: A list of constraint violations.
        all_vars: List of variable names.
        constraint_coeffs: Coefficients for each constraint.
    """
    print("Constraint Violations Detected:")
    for (idx, lhs_value, rhs_value, constraint_type) in violations:
        # Construct the constraint as a string using the variable names and coefficients
        constraint_str = " + ".join(f"{coeff}*{all_vars[j]}" for j, coeff in enumerate(constraint_coeffs[idx]) if coeff != 0)
        print(f"Constraint {idx + 1}: {constraint_str} {constraint_type} {rhs_value}, but LHS = {lhs_value}")




def generalized_penalty_check(tableau, all_vars, artificial_vars, M, tableau_metadata):
    penalty_m_term, constant_value, feasible = 0, tableau[-1, -1], True

    for i in artificial_vars:
        if i in tableau_metadata["basis"]:
            row_idx = tableau_metadata["basis"].index(i)
            value_in_basis = tableau[row_idx, -1]
            if value_in_basis > 0:
                penalty_m_term += value_in_basis
                feasible = False

    if not feasible:
        print(f"Penalty term due to artificial variables: {penalty_m_term} * M")
        constant_value += penalty_m_term * M

    return penalty_m_term, constant_value, feasible



In [1]:
!pip install pulp

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.7/17.7 MB 56.9 MB/s eta 0:00:00


In [27]:
import numpy as np
from pulp import LpMinimize, LpProblem, LpVariable, lpSum
from fractions import Fraction

# Define the data
MAX_ITERATIONS = 1000
num_vars = 3
objective_coeffs = [5000, 4000, 6000]
num_constraints = 3
constraint_coeffs = [
    [3, 2, 1],  # Coefficients for constraint 1
    [1, 4, 3],  # Coefficients for constraint 2
    [1, 2, 2]   # Coefficients for constraint 3 (>= type)
]
constraint_types = ['<=', '<=', '>=']  # Types of constraints
b_values = [1200, 1500, 800]

# Create the initial tableau for minimization
tableau, tableau_metadata = create_tableau_only_for_minimization(
    num_vars, objective_coeffs, num_constraints,
    constraint_coeffs, constraint_types, b_values
)

# Add original constraints into tableau_metadata for validation later
tableau_metadata["constraints"] = {
    "coeffs": constraint_coeffs,
    "types": constraint_types,
    "rhs": b_values
}

# Extract metadata
basis = tableau_metadata["basis"]
all_vars = tableau_metadata["all_vars"]
coeffs = tableau_metadata["coeffs"]

# Extract artificial variables from the all_vars list
artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

# Print initial tableau
print("\nInitial Tableau:")
print_tableau_minimization(tableau, all_vars, basis, coeffs, constraint_types)
print("Initial Basis Indices:", basis)
print("Initial Basis Variables and Their Values:")
for row_idx, var_idx in enumerate(basis):
    var_name = all_vars[var_idx]
    value = 1e6 if var_idx in artificial_vars else tableau[row_idx, -1]
    print(f"Variable {var_name} (Index {var_idx}): Value = {value}")

# Perform simplex iterations until an optimal solution is reached or the solution is found to be unbounded
is_optimal = False
is_unbounded = False
iteration_count = 0

# Track previous tableau states to detect cycling
previous_basis_states = []

while not is_optimal and not is_unbounded:
    # Identify the entering column
    entering_column = identify_entering_column_minimization(tableau)
    if entering_column is None:
        is_optimal = True
        break

    # Identify the leaving row
    leaving_row = identify_leaving_row_minimization(tableau, entering_column)
    if leaving_row is None:
        is_unbounded = True
        break

    # Perform pivot operation
    pivot_element = locate_pivot_element_minimization(tableau, entering_column, leaving_row)
    tableau = update_key_row_minimization(tableau, leaving_row, pivot_element)
    tableau = update_non_key_rows_minimization(tableau, entering_column, leaving_row)

    # Update the basis with the new entering variable
    update_basis_with_values(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars)

    # Zero out artificial variables when they leave the basis
    if tableau_metadata["basis"][leaving_row] in artificial_vars:
        tableau[:, tableau_metadata["basis"][leaving_row]] = 0  # Zero out column of leaving artificial variable
        tableau_metadata["coeffs"][tableau_metadata["basis"][leaving_row]] = 0  # Zero out the coefficient

    # Continue with updating the objective row
    update_objective_row_minimization(tableau, tableau_metadata["coeffs"], tableau_metadata["basis"], artificial_vars, all_vars)

    # Print or display the updated tableau for debugging
    print_tableau_minimization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types)

    # Update iteration count to prevent infinite loops
    iteration_count += 1
    if iteration_count > MAX_ITERATIONS:
        print("Max iterations reached, stopping.")
        break

# Define the Big M value (Large penalty)
M = 1e6  # Example value for M

# Perform simplex iterations and find the optimal solution
if is_optimal:
    print("\nOptimal Solution Reached (Custom Simplex Method)")

    # Check for feasibility and apply penalties using the Big M value
    penalty_m, optimal_value, is_feasible = check_penalty_and_feasibility_minimization(tableau, all_vars, artificial_vars, M, tableau_metadata)

    # Extract the solution from the basic variables
    solution = {}
    for i in range(num_vars):
        if i in tableau_metadata["basis"]:
            row = tableau_metadata["basis"].index(i)
            solution[f"x{i+1}"] = Fraction(tableau[row, -1]).limit_denominator()
        else:
            solution[f"x{i+1}"] = 0

    # Calculate the unpenalized objective value
    unpenalized_objective_value = sum(objective_coeffs[i] * solution[f"x{i+1}"] for i in range(num_vars))

    # Print the objective value without penalties
    print(f"Objective Value (without penalty): Z = {unpenalized_objective_value}")

    # Now handle the penalty due to artificial variables
    if not is_feasible:
        print(f"Warning: Artificial variables are still in the basis, the solution might be infeasible.")
        print(f"Optimal Objective Value: Z = {penalty_m}M + {unpenalized_objective_value}")

    # Print the final solution
    print("Solution:", solution)

    # Check for constraint violations dynamically
    violations = check_constraint_violations(solution, tableau_metadata["constraints"]["coeffs"], tableau_metadata["constraints"]["types"], tableau_metadata["constraints"]["rhs"])
    if violations:
        print_violation_report(violations, all_vars, tableau_metadata["constraints"]["coeffs"])
    else:
        print("All constraints are satisfied.")

elif is_unbounded:
    print("\nThe solution is unbounded.")


# Solve with Pulp to compare
model = LpProblem(name="Minimization_Problem", sense=LpMinimize)
x = {i: LpVariable(name=f"x{i+1}", lowBound=0) for i in range(num_vars)}
model += lpSum(objective_coeffs[i] * x[i] for i in range(num_vars))
for i in range(num_constraints):
    if constraint_types[i] == '<=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) <= b_values[i]
    elif constraint_types[i] == '>=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) >= b_values[i]
    elif constraint_types[i] == '=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) == b_values[i]

model.solve()

print("\nOptimal Solution Reached (Pulp)")
for var in x.values():
    print(f"{var.name}: {var.value()}")
print("Objective Value:", model.objective.value())



Initial Tableau:
╒═══════════════════╤═════════╤═════════╤════════════════╤══════════╤══════╤══════╤════════════╤══════╤════════════╕
│ Constraint Type   │ BASIS   │ x1      │ x2             │ x3       │ s1   │ s2   │ surplus3   │ a3   │ RHS        │
╞═══════════════════╪═════════╪═════════╪════════════════╪══════════╪══════╪══════╪════════════╪══════╪════════════╡
│ BASIS             │ s1 = 0  │ s2 = 0  │ a3 = 1000000.0 │          │      │      │            │      │            │
├───────────────────┼─────────┼─────────┼────────────────┼──────────┼──────┼──────┼────────────┼──────┼────────────┤
│ Coeff             │ 5000    │ 4000    │ 6000           │ 0        │ 0    │ 0    │ 1000000    │      │            │
├───────────────────┼─────────┼─────────┼────────────────┼──────────┼──────┼──────┼────────────┼──────┼────────────┤
│ <=                │ s1      │ 3       │ 2              │ 1        │ 1    │ 0    │ 0          │ 0    │ 1200       │
├───────────────────┼─────────┼─────────┼─────

In [28]:
import numpy as np
from pulp import LpMinimize, LpProblem, LpVariable, lpSum
from fractions import Fraction

# Define the data
MAX_ITERATIONS = 1000
num_vars = 10
objective_coeffs = [5, 3, 4, 6, 2, 7, 9, 4, 8, 10]
num_constraints = 12
constraint_coeffs = [
    [2, 3, 1, 5, 1, 4, 1, 1, 2, 1],
    [4, 1, 3, 1, 2, 1, 5, 1, 2, 3],
    [1, 1, 2, 3, 4, 1, 5, 3, 1, 1],
    [3, 2, 4, 1, 1, 3, 2, 4, 1, 2],
    [1, 2, 3, 4, 5, 1, 1, 1, 2, 3],
    [2, 3, 1, 1, 2, 5, 1, 4, 1, 1],
    [1, 4, 5, 2, 3, 6, 3, 1, 2, 1],
    [5, 1, 2, 1, 3, 4, 1, 1, 2, 5],
    [4, 2, 3, 1, 1, 2, 3, 4, 1, 1],
    [3, 1, 2, 5, 1, 4, 1, 1, 1, 2],
    [1, 1, 4, 3, 5, 1, 1, 1, 2, 3],
    [2, 3, 4, 1, 1, 2, 1, 5, 1, 2]
]
constraint_types = ['<=', '>=', '=', '<=', '>=', '=', '<=', '>=', '=', '<=', '>=', '=']
b_values = [50, 40, 30, 60, 45, 50, 55, 35, 40, 70, 50, 65]

# Create the initial tableau for minimization
tableau, tableau_metadata = create_tableau_only_for_minimization(
    num_vars, objective_coeffs, num_constraints,
    constraint_coeffs, constraint_types, b_values
)

# Add original constraints into tableau_metadata for validation later
tableau_metadata["constraints"] = {
    "coeffs": constraint_coeffs,
    "types": constraint_types,
    "rhs": b_values
}

# Extract metadata
basis = tableau_metadata["basis"]
all_vars = tableau_metadata["all_vars"]
coeffs = tableau_metadata["coeffs"]

# Extract artificial variables from the all_vars list
artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

# Print initial tableau
print("\nInitial Tableau:")
print_tableau_minimization(tableau, all_vars, basis, coeffs, constraint_types)
print("Initial Basis Indices:", basis)
print("Initial Basis Variables and Their Values:")
for row_idx, var_idx in enumerate(basis):
    var_name = all_vars[var_idx]
    value = 1e6 if var_idx in artificial_vars else tableau[row_idx, -1]
    print(f"Variable {var_name} (Index {var_idx}): Value = {value}")

# Perform simplex iterations until an optimal solution is reached or the solution is found to be unbounded
is_optimal = False
is_unbounded = False
iteration_count = 0

# Track previous tableau states to detect cycling
previous_basis_states = []

while not is_optimal and not is_unbounded:
    # Identify the entering column
    entering_column = identify_entering_column_minimization(tableau)
    if entering_column is None:
        is_optimal = True
        break

    # Identify the leaving row
    leaving_row = identify_leaving_row_minimization(tableau, entering_column)
    if leaving_row is None:
        is_unbounded = True
        break

    # Perform pivot operation
    pivot_element = locate_pivot_element_minimization(tableau, entering_column, leaving_row)
    tableau = update_key_row_minimization(tableau, leaving_row, pivot_element)
    tableau = update_non_key_rows_minimization(tableau, entering_column, leaving_row)

    # Update the basis with the new entering variable
    update_basis_with_values(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars)

    # Zero out artificial variables when they leave the basis
    if tableau_metadata["basis"][leaving_row] in artificial_vars:
        tableau[:, tableau_metadata["basis"][leaving_row]] = 0  # Zero out column of leaving artificial variable
        tableau_metadata["coeffs"][tableau_metadata["basis"][leaving_row]] = 0  # Zero out the coefficient

    # Continue with updating the objective row
    update_objective_row_minimization(tableau, tableau_metadata["coeffs"], tableau_metadata["basis"], artificial_vars, all_vars)

    # Print or display the updated tableau for debugging
    print_tableau_minimization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types)

    # Update iteration count to prevent infinite loops
    iteration_count += 1
    if iteration_count > MAX_ITERATIONS:
        print("Max iterations reached, stopping.")
        break

# Define the Big M value (Large penalty)
M = 1e6  # Example value for M

# Perform simplex iterations and find the optimal solution
if is_optimal:
    print("\nOptimal Solution Reached (Custom Simplex Method)")

    # Check for feasibility and apply penalties using the Big M value
    penalty_m, optimal_value, is_feasible = check_penalty_and_feasibility_minimization(tableau, all_vars, artificial_vars, M, tableau_metadata)

    # Extract the solution from the basic variables
    solution = {}
    for i in range(num_vars):
        if i in tableau_metadata["basis"]:
            row = tableau_metadata["basis"].index(i)
            solution[f"x{i+1}"] = Fraction(tableau[row, -1]).limit_denominator()
        else:
            solution[f"x{i+1}"] = 0

    # Calculate the unpenalized objective value
    unpenalized_objective_value = sum(objective_coeffs[i] * solution[f"x{i+1}"] for i in range(num_vars))

    # Print the objective value without penalties
    print(f"Objective Value (without penalty): Z = {unpenalized_objective_value}")

    # Now handle the penalty due to artificial variables
    if not is_feasible:
        print(f"Warning: Artificial variables are still in the basis, the solution might be infeasible.")
        print(f"Optimal Objective Value: Z = {penalty_m}M + {unpenalized_objective_value}")

    # Print the final solution
    print("Solution:", solution)

    # Check for constraint violations dynamically
    violations = check_constraint_violations(solution, tableau_metadata["constraints"]["coeffs"], tableau_metadata["constraints"]["types"], tableau_metadata["constraints"]["rhs"])
    if violations:
        print_violation_report(violations, all_vars, tableau_metadata["constraints"]["coeffs"])
    else:
        print("All constraints are satisfied.")

elif is_unbounded:
    print("\nThe solution is unbounded.")


# Solve with Pulp to compare
model = LpProblem(name="Minimization_Problem", sense=LpMinimize)
x = {i: LpVariable(name=f"x{i+1}", lowBound=0) for i in range(num_vars)}
model += lpSum(objective_coeffs[i] * x[i] for i in range(num_vars))
for i in range(num_constraints):
    if constraint_types[i] == '<=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) <= b_values[i]
    elif constraint_types[i] == '>=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) >= b_values[i]
    elif constraint_types[i] == '=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) == b_values[i]

model.solve()

print("\nOptimal Solution Reached (Pulp)")
for var in x.values():
    print(f"{var.name}: {var.value()}")
print("Objective Value:", model.objective.value())




Initial Tableau:
╒═══════════════════╤═════════╤════════════════╤════════════════╤═══════════╤════════════════╤════════════════╤═══════════╤════════════════╤════════════════╤═══════════╤═════════════════╤═════════════════╤════════════╤═════════╤══════╤══════╤════════════╤═════════╤══════╤══════╤════════════╤═════════╤══════╤═══════╤═════════════╤═════════╤═══════╤════════════╕
│ Constraint Type   │ BASIS   │ x1             │ x2             │ x3        │ x4             │ x5             │ x6        │ x7             │ x8             │ x9        │ x10             │ s1              │ surplus2   │ a2      │ a3   │ s4   │ surplus5   │ a5      │ a6   │ s7   │ surplus8   │ a8      │ a9   │ s10   │ surplus11   │ a11     │ a12   │ RHS        │
╞═══════════════════╪═════════╪════════════════╪════════════════╪═══════════╪════════════════╪════════════════╪═══════════╪════════════════╪════════════════╪═══════════╪═════════════════╪═════════════════╪════════════╪═════════╪══════╪══════╪════════════╪═

In [25]:
import numpy as np
from pulp import LpMinimize, LpProblem, LpVariable, lpSum
from fractions import Fraction

# Define the data
MAX_ITERATIONS = 1000
num_vars = 40
objective_coeffs = objective_coeffs = [5, 3, 4, 6, 2, 7, 9, 4, 8, 10, 12, 14, 15, 1, 7, 11, 5, 9, 13, 6,
                    10, 8, 5, 7, 2, 12, 13, 1, 9, 4, 3, 6, 11, 7, 15, 5, 4, 9, 8, 10]
num_constraints = 35
constraint_coeffs = constraint_coeffs = [
    [2, 3, 1, 5, 1, 4, 1, 1, 2, 1, 3, 2, 4, 1, 1, 5, 4, 3, 1, 2, 3, 2, 4, 1, 1, 3, 4, 2, 1, 3, 1, 2, 4, 3, 1, 4, 2, 1, 3, 5],
    [4, 1, 3, 1, 2, 1, 5, 1, 2, 3, 5, 2, 3, 1, 4, 3, 2, 1, 3, 2, 4, 3, 5, 1, 2, 3, 4, 5, 2, 3, 1, 2, 3, 1, 2, 4, 3, 2, 1, 4],
    [1, 1, 2, 3, 4, 1, 5, 3, 1, 1, 4, 3, 2, 4, 1, 1, 2, 4, 5, 3, 2, 4, 1, 1, 5, 2, 1, 3, 2, 4, 1, 5, 4, 2, 3, 1, 4, 5, 3, 1],
    [3, 4, 2, 1, 5, 3, 2, 4, 1, 5, 3, 1, 2, 4, 5, 3, 2, 4, 1, 5, 4, 3, 1, 2, 3, 5, 4, 1, 3, 2, 1, 5, 3, 4, 1, 2, 5, 3, 2, 4],
    [1, 5, 2, 4, 3, 2, 5, 1, 2, 4, 5, 3, 4, 1, 2, 5, 1, 3, 2, 5, 3, 1, 4, 2, 5, 1, 2, 3, 4, 1, 3, 5, 1, 2, 4, 3, 5, 2, 1, 4],
    [5, 3, 1, 4, 2, 3, 5, 2, 4, 5, 1, 2, 5, 3, 2, 4, 1, 5, 3, 4, 2, 5, 1, 2, 4, 3, 1, 5, 2, 1, 5, 3, 2, 4, 5, 1, 4, 3, 2, 5],
    [4, 2, 3, 5, 1, 4, 2, 5, 3, 2, 5, 1, 3, 4, 5, 2, 3, 5, 1, 2, 5, 4, 3, 1, 4, 5, 3, 1, 2, 4, 1, 5, 2, 3, 1, 4, 2, 5, 3, 4],
    [1, 4, 5, 2, 3, 1, 5, 3, 1, 5, 2, 3, 5, 1, 2, 4, 5, 1, 3, 4, 1, 2, 4, 5, 3, 1, 4, 2, 5, 1, 3, 2, 4, 1, 3, 5, 2, 5, 1, 3],
    [2, 3, 1, 5, 1, 3, 4, 1, 2, 5, 4, 3, 1, 5, 4, 2, 1, 3, 5, 1, 4, 2, 1, 5, 3, 4, 5, 2, 1, 3, 5, 2, 4, 1, 3, 5, 2, 1, 4, 3],
    [3, 1, 4, 5, 2, 3, 1, 5, 4, 2, 1, 5, 3, 2, 4, 1, 5, 2, 1, 4, 5, 3, 2, 1, 5, 4, 2, 1, 3, 5, 4, 2, 1, 5, 3, 1, 4, 2, 5, 3],
    [4, 3, 1, 2, 5, 4, 3, 1, 5, 2, 1, 3, 5, 2, 4, 1, 5, 3, 1, 2, 5, 4, 1, 5, 3, 2, 4, 1, 3, 5, 1, 4, 3, 2, 5, 4, 1, 3, 5, 2],
    [1, 4, 2, 3, 5, 1, 3, 4, 5, 2, 3, 1, 5, 2, 4, 5, 1, 3, 2, 5, 1, 4, 5, 2, 3, 1, 5, 4, 3, 2, 1, 5, 3, 4, 1, 5, 2, 4, 3, 5],
    [5, 1, 3, 2, 4, 5, 1, 4, 2, 5, 3, 1, 5, 4, 3, 1, 2, 5, 3, 1, 5, 2, 4, 1, 3, 5, 4, 1, 5, 3, 2, 1, 4, 5, 2, 1, 3, 5, 1, 4],
    [2, 5, 3, 4, 1, 5, 2, 3, 5, 1, 4, 2, 5, 1, 4, 3, 2, 5, 1, 5, 3, 2, 4, 1, 5, 2, 1, 5, 4, 3, 1, 5, 2, 1, 4, 5, 2, 1, 3, 5],
    [3, 1, 5, 2, 4, 3, 1, 5, 2, 4, 1, 3, 5, 2, 4, 1, 3, 2, 5, 1, 4, 3, 2, 5, 1, 3, 4, 2, 5, 1, 5, 4, 3, 1, 5, 2, 1, 5, 4, 3],
    [4, 5, 1, 2, 5, 4, 1, 3, 5, 2, 1, 5, 3, 2, 1, 4, 5, 1, 3, 4, 1, 5, 2, 3, 5, 1, 5, 4, 1, 3, 5, 2, 1, 4, 3, 5, 1, 5, 2, 4],
    [2, 1, 4, 5, 3, 2, 5, 1, 4, 5, 1, 3, 2, 5, 4, 1, 5, 1, 2, 5, 3, 1, 5, 2, 4, 1, 3, 5, 4, 1, 2, 3, 5, 1, 4, 3, 5, 2, 1, 5],
    [5, 3, 1, 2, 4, 5, 2, 1, 4, 5, 1, 5, 2, 3, 4, 1, 5, 1, 4, 3, 5, 2, 4, 1, 5, 3, 1, 5, 2, 4, 1, 5, 2, 1, 4, 3, 5, 4, 1, 2],
    [3, 4, 2, 5, 1, 3, 4, 1, 5, 2, 4, 1, 5, 3, 2, 1, 5, 3, 1, 4, 5, 2, 1, 5, 3, 4, 1, 2, 5, 3, 2, 4, 1, 5, 3, 1, 4, 5, 2, 3],
    [4, 3, 1, 5, 4, 2, 3, 5, 1, 2, 3, 4, 5, 2, 1, 3, 4, 1, 2, 5, 1, 5, 3, 1, 4, 5, 3, 2, 1, 5, 2, 1, 5, 4, 3, 5, 2, 4, 1, 3],
    [1, 5, 2, 4, 3, 2, 5, 1, 4, 5, 2, 3, 1, 5, 4, 2, 1, 5, 1, 4, 5, 3, 1, 5, 2, 4, 1, 3, 5, 1, 2, 5, 4, 1, 3, 5, 1, 4, 2, 5],
    [5, 4, 3, 1, 2, 5, 4, 2, 5, 1, 3, 2, 1, 5, 4, 3, 1, 5, 2, 4, 1, 5, 2, 3, 4, 1, 5, 3, 4, 1, 5, 2, 1, 4, 5, 2, 1, 3, 5, 1],
    [3, 5, 2, 1, 4, 3, 1, 5, 2, 4, 5, 3, 1, 5, 2, 4, 5, 1, 2, 5, 3, 4, 1, 5, 2, 4, 5, 3, 2, 1, 5, 4, 1, 3, 2, 5, 1, 3, 4, 5],
    [2, 4, 5, 1, 3, 5, 1, 4, 3, 5, 2, 1, 5, 4, 1, 3, 5, 2, 1, 5, 4, 3, 5, 1, 2, 4, 3, 5, 2, 1, 5, 4, 3, 1, 5, 2, 1, 5, 4, 3],
    [5, 2, 1, 5, 4, 3, 2, 1, 5, 4, 1, 5, 3, 4, 5, 2, 1, 5, 3, 1, 5, 4, 2, 1, 5, 3, 1, 5, 4, 3, 2, 5, 1, 4, 3, 1, 5, 2, 1, 4],
    [1, 3, 2, 5, 4, 1, 5, 2, 3, 5, 1, 4, 3, 2, 1, 5, 4, 1, 5, 3, 2, 1, 5, 4, 2, 1, 3, 5, 4, 1, 5, 2, 1, 4, 3, 5, 1, 5, 3, 2],
    [3, 1, 4, 5, 2, 3, 1, 5, 2, 4, 5, 3, 2, 5, 1, 4, 3, 2, 1, 5, 4, 5, 1, 2, 3, 4, 1, 5, 2, 3, 5, 4, 1, 5, 2, 1, 4, 3, 5, 1],
    [5, 4, 3, 1, 5, 2, 4, 3, 5, 1, 2, 3, 4, 1, 5, 2, 1, 5, 3, 2, 4, 5, 1, 2, 5, 4, 3, 1, 5, 2, 1, 3, 4, 5, 1, 5, 3, 2, 4, 1],
    [1, 5, 4, 2, 3, 5, 1, 3, 4, 5, 2, 1, 5, 3, 4, 1, 5, 2, 1, 4, 5, 2, 5, 1, 3, 4, 5, 2, 1, 3, 5, 4, 1, 5, 2, 1, 5, 4, 3, 2],
    [2, 1, 3, 4, 5, 2, 4, 5, 1, 3, 5, 1, 2, 5, 4, 3, 2, 1, 5, 4, 3, 2, 5, 1, 5, 3, 4, 2, 1, 5, 1, 4, 3, 2, 5, 1, 3, 4, 2, 1],
    [5, 2, 1, 5, 3, 4, 1, 5, 2, 1, 3, 4, 5, 2, 1, 5, 4, 1, 5, 2, 1, 4, 5, 1, 3, 5, 2, 4, 5, 1, 2, 5, 1, 4, 3, 5, 1, 2, 3, 4],
    [4, 3, 1, 2, 5, 1, 4, 5, 2, 3, 4, 5, 1, 3, 4, 2, 5, 1, 2, 4, 5, 3, 1, 5, 2, 3, 4, 1, 5, 2, 1, 5, 3, 1, 4, 5, 3, 2, 1, 4],
    [1, 5, 4, 2, 3, 5, 1, 4, 5, 2, 3, 1, 5, 4, 2, 1, 5, 1, 2, 4, 3, 1, 5, 2, 5, 1, 3, 4, 5, 2, 1, 5, 4, 1, 3, 5, 2, 5, 1, 4],
    [3, 4, 1, 2, 5, 3, 4, 5, 1, 2, 5, 3, 1, 4, 5, 3, 2, 4, 1, 5, 3, 1, 4, 2, 5, 3, 4, 1, 5, 3, 1, 4, 2, 1, 5, 3, 1, 4, 5, 2],
    [5, 2, 1, 5, 3, 2, 5, 1, 4, 5, 3, 1, 2, 5, 1, 4, 5, 3, 2, 5, 1, 3, 4, 1, 5, 2, 5, 1, 3, 4, 2, 5, 1, 5, 3, 1, 4, 2, 5, 1],
    [4, 1, 5, 3, 1, 4, 5, 2, 5, 1, 4, 3, 5, 1, 2, 5, 4, 1, 2, 5, 3, 1, 4, 5, 3, 1, 4, 2, 5, 3, 1, 4, 1, 5, 4, 3, 2, 5, 1, 2],
]

constraint_types = [
    '<=', '>=', '=', '<=', '>=', '=', '<=', '>=', '=', '<=',  # First 10 constraint types
    '<=', '>=', '=', '<=', '>=', '=', '<=', '>=', '=', '<=',  # Second set of 10 constraint types
    '<=', '>=', '=', '<=', '>=', '=', '<=', '>=', '=', '<=', '=', '<=', '>=', '<=', '<='   # Final 15 constraint types
]


b_values = [100, 200, 150, 120, 250, 180, 300, 130, 220, 170, 160, 140, 110, 210, 190,
            240, 260, 230, 270, 280, 290, 310, 320, 330, 340, 350, 360, 370, 380, 390,
            400, 410, 420, 430, 440]

# Create the initial tableau for minimization
tableau, tableau_metadata = create_tableau_only_for_minimization(
    num_vars, objective_coeffs, num_constraints,
    constraint_coeffs, constraint_types, b_values
)

# Add original constraints into tableau_metadata for validation later
tableau_metadata["constraints"] = {
    "coeffs": constraint_coeffs,
    "types": constraint_types,
    "rhs": b_values
}

# Extract metadata
basis = tableau_metadata["basis"]
all_vars = tableau_metadata["all_vars"]
coeffs = tableau_metadata["coeffs"]

# Extract artificial variables from the all_vars list
artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

# Print initial tableau
print("\nInitial Tableau:")
print_tableau_minimization(tableau, all_vars, basis, coeffs, constraint_types)
print("Initial Basis Indices:", basis)
print("Initial Basis Variables and Their Values:")
for row_idx, var_idx in enumerate(basis):
    var_name = all_vars[var_idx]
    value = 1e6 if var_idx in artificial_vars else tableau[row_idx, -1]
    print(f"Variable {var_name} (Index {var_idx}): Value = {value}")

# Perform simplex iterations until an optimal solution is reached or the solution is found to be unbounded
is_optimal = False
is_unbounded = False
iteration_count = 0

# Track previous tableau states to detect cycling
previous_basis_states = []

while not is_optimal and not is_unbounded:
    # Identify the entering column
    entering_column = identify_entering_column_minimization(tableau)
    if entering_column is None:
        is_optimal = True
        break

    # Identify the leaving row
    leaving_row = identify_leaving_row_minimization(tableau, entering_column)
    if leaving_row is None:
        is_unbounded = True
        break

    # Perform pivot operation
    pivot_element = locate_pivot_element_minimization(tableau, entering_column, leaving_row)
    tableau = update_key_row_minimization(tableau, leaving_row, pivot_element)
    tableau = update_non_key_rows_minimization(tableau, entering_column, leaving_row)

    # Update the basis with the new entering variable
    update_basis_with_values(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars)

    # Zero out artificial variables when they leave the basis
    if tableau_metadata["basis"][leaving_row] in artificial_vars:
        tableau[:, tableau_metadata["basis"][leaving_row]] = 0  # Zero out column of leaving artificial variable
        tableau_metadata["coeffs"][tableau_metadata["basis"][leaving_row]] = 0  # Zero out the coefficient

    # Continue with updating the objective row
    update_objective_row_minimization(tableau, tableau_metadata["coeffs"], tableau_metadata["basis"], artificial_vars, all_vars)

    # Print or display the updated tableau for debugging
    print_tableau_minimization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types)

    # Update iteration count to prevent infinite loops
    iteration_count += 1
    if iteration_count > MAX_ITERATIONS:
        print("Max iterations reached, stopping.")
        break

# Define the Big M value (Large penalty)
M = 1e6  # Example value for M

# Perform simplex iterations and find the optimal solution
if is_optimal:
    print("\nOptimal Solution Reached (Custom Simplex Method)")

    # Check for feasibility and apply penalties using the Big M value
    penalty_m, optimal_value, is_feasible = check_penalty_and_feasibility_minimization(tableau, all_vars, artificial_vars, M, tableau_metadata)

    # Extract the solution from the basic variables
    solution = {}
    for i in range(num_vars):
        if i in tableau_metadata["basis"]:
            row = tableau_metadata["basis"].index(i)
            solution[f"x{i+1}"] = Fraction(tableau[row, -1]).limit_denominator()
        else:
            solution[f"x{i+1}"] = 0

    # Calculate the unpenalized objective value
    unpenalized_objective_value = sum(objective_coeffs[i] * solution[f"x{i+1}"] for i in range(num_vars))

    # Print the objective value without penalties
    print(f"Objective Value (without penalty): Z = {unpenalized_objective_value}")

    # Now handle the penalty due to artificial variables
    if not is_feasible:
        print(f"Warning: Artificial variables are still in the basis, the solution might be infeasible.")
        print(f"Optimal Objective Value: Z = {penalty_m}M + {unpenalized_objective_value}")

    # Print the final solution
    print("Solution:", solution)

    # Check for constraint violations dynamically
    violations = check_constraint_violations(solution, tableau_metadata["constraints"]["coeffs"], tableau_metadata["constraints"]["types"], tableau_metadata["constraints"]["rhs"])
    if violations:
        print_violation_report(violations, all_vars, tableau_metadata["constraints"]["coeffs"])
    else:
        print("All constraints are satisfied.")

elif is_unbounded:
    print("\nThe solution is unbounded.")


# Solve with Pulp to compare
model = LpProblem(name="Minimization_Problem", sense=LpMinimize)
x = {i: LpVariable(name=f"x{i+1}", lowBound=0) for i in range(num_vars)}
model += lpSum(objective_coeffs[i] * x[i] for i in range(num_vars))
for i in range(num_constraints):
    if constraint_types[i] == '<=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) <= b_values[i]
    elif constraint_types[i] == '>=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) >= b_values[i]
    elif constraint_types[i] == '=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) == b_values[i]

model.solve()

print("\nOptimal Solution Reached (Pulp)")
for var in x.values():
    print(f"{var.name}: {var.value()}")
print("Objective Value:", model.objective.value())



Initial Tableau:
╒═══════════════════╤═════════╤════════════════╤════════════════╤═══════════╤════════════════╤════════════════╤═══════════╤════════════════╤════════════════╤═══════════╤═══════════╤═════════════════╤═════════════════╤═══════════╤═════════════════╤═════════════════╤═══════════╤═════════════════╤═════════════════╤═══════════╤═══════════╤═════════════════╤═════════════════╤═══════════╤═════════════════╤═════════════════╤═══════════╤═════════════════╤═════════════════╤═══════════╤═════════════════╤═══════════╤═════════════════╤═══════════╤═══════════╤═══════════╤═══════════╤═══════════╤═══════════╤═══════════╤═══════════╤══════╤════════════╤═════════╤══════╤══════╤════════════╤═════════╤══════╤══════╤════════════╤═════════╤══════╤═══════╤═══════╤═════════════╤═════════╤═══════╤═══════╤═════════════╤═════════╤═══════╤═══════╤═════════════╤═════════╤═══════╤═══════╤═══════╤═════════════╤═════════╤═══════╤═══════╤═════════════╤═════════╤═══════╤═══════╤═════════════╤════════

In [29]:
import numpy as np
from pulp import LpMinimize, LpProblem, LpVariable, lpSum
from fractions import Fraction

# Define the data
MAX_ITERATIONS = 1000
# Define the problem
num_vars = 15
objective_coeffs = [3, 5, 2, 7, 4, 6, 8, 3, 9, 1, 7, 5, 6, 4, 8]
num_constraints = 16
constraint_coeffs = [
    [1, 2, 3, 0, 0, 1, 2, 1, 3, 1, 0, 2, 4, 5, 1],  # Example constraint 1
    [0, 1, 1, 3, 2, 0, 1, 0, 1, 0, 3, 4, 2, 2, 3],  # Example constraint 2
    [2, 0, 3, 1, 1, 2, 0, 1, 0, 4, 1, 3, 2, 3, 1],  # Example constraint 3
    [1, 1, 0, 2, 1, 3, 2, 0, 5, 1, 2, 3, 0, 4, 2],  # Example constraint 4
    [0, 3, 1, 1, 2, 0, 1, 3, 2, 3, 1, 1, 3, 1, 2],  # Example constraint 5
    [2, 1, 0, 3, 1, 1, 2, 1, 4, 2, 3, 0, 1, 0, 3],  # Example constraint 6
    [3, 2, 1, 0, 3, 4, 1, 2, 1, 0, 5, 2, 1, 3, 1],  # Example constraint 7
    [0, 1, 3, 2, 0, 5, 1, 3, 4, 1, 2, 0, 3, 4, 5],  # Example constraint 8
    [4, 2, 0, 1, 3, 2, 5, 1, 0, 1, 3, 2, 1, 0, 2],  # Example constraint 9
    [1, 0, 2, 3, 1, 0, 4, 3, 1, 2, 3, 5, 4, 1, 2],  # Example constraint 10
    [3, 1, 1, 4, 0, 2, 1, 3, 2, 1, 4, 2, 3, 5, 1],  # Example constraint 11
    [2, 3, 0, 1, 2, 3, 4, 5, 1, 0, 2, 1, 0, 3, 2],  # Example constraint 12
    [1, 4, 3, 2, 0, 1, 5, 3, 0, 4, 1, 2, 5, 1, 3],  # Example constraint 13
    [3, 0, 2, 1, 3, 4, 2, 0, 5, 1, 3, 0, 2, 4, 1],  # Example constraint 14
    [2, 5, 1, 0, 4, 3, 1, 2, 3, 0, 4, 1, 3, 2, 5],  # Example constraint 15
    [0, 2, 4, 3, 1, 5, 3, 1, 0, 1, 2, 3, 4, 1, 2]   # Example constraint 16
]
constraint_types = ['<=', '<=', '>=', '=', '<=', '>=', '<=', '>=', '<=', '>=', '<=', '<=', '>=', '=', '<=', '>=']
b_values = [25, 30, 40, 15, 50, 10, 60, 45, 55, 35, 20, 25, 50, 15, 45, 30]

# Create the initial tableau for minimization
tableau, tableau_metadata = create_tableau_only_for_minimization(
    num_vars, objective_coeffs, num_constraints,
    constraint_coeffs, constraint_types, b_values
)

# Add original constraints into tableau_metadata for validation later
tableau_metadata["constraints"] = {
    "coeffs": constraint_coeffs,
    "types": constraint_types,
    "rhs": b_values
}

# Extract metadata
basis = tableau_metadata["basis"]
all_vars = tableau_metadata["all_vars"]
coeffs = tableau_metadata["coeffs"]

# Extract artificial variables from the all_vars list
artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

# Print initial tableau
print("\nInitial Tableau:")
print_tableau_minimization(tableau, all_vars, basis, coeffs, constraint_types)
print("Initial Basis Indices:", basis)
print("Initial Basis Variables and Their Values:")
for row_idx, var_idx in enumerate(basis):
    var_name = all_vars[var_idx]
    value = 1e6 if var_idx in artificial_vars else tableau[row_idx, -1]
    print(f"Variable {var_name} (Index {var_idx}): Value = {value}")

# Perform simplex iterations until an optimal solution is reached or the solution is found to be unbounded
is_optimal = False
is_unbounded = False
iteration_count = 0

# Track previous tableau states to detect cycling
previous_basis_states = []

while not is_optimal and not is_unbounded:
    # Identify the entering column
    entering_column = identify_entering_column_minimization(tableau)
    if entering_column is None:
        is_optimal = True
        break

    # Identify the leaving row
    leaving_row = identify_leaving_row_minimization(tableau, entering_column)
    if leaving_row is None:
        is_unbounded = True
        break

    # Perform pivot operation
    pivot_element = locate_pivot_element_minimization(tableau, entering_column, leaving_row)
    tableau = update_key_row_minimization(tableau, leaving_row, pivot_element)
    tableau = update_non_key_rows_minimization(tableau, entering_column, leaving_row)

    # Update the basis with the new entering variable
    update_basis_with_values(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars)

    # Zero out artificial variables when they leave the basis
    if tableau_metadata["basis"][leaving_row] in artificial_vars:
        tableau[:, tableau_metadata["basis"][leaving_row]] = 0  # Zero out column of leaving artificial variable
        tableau_metadata["coeffs"][tableau_metadata["basis"][leaving_row]] = 0  # Zero out the coefficient

    # Continue with updating the objective row
    update_objective_row_minimization(tableau, tableau_metadata["coeffs"], tableau_metadata["basis"], artificial_vars, all_vars)

    # Print or display the updated tableau for debugging
    print_tableau_minimization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types)

    # Update iteration count to prevent infinite loops
    iteration_count += 1
    if iteration_count > MAX_ITERATIONS:
        print("Max iterations reached, stopping.")
        break

# Define the Big M value (Large penalty)
M = 1e6  # Example value for M

# Perform simplex iterations and find the optimal solution
if is_optimal:
    print("\nOptimal Solution Reached (Custom Simplex Method)")

    # Check for feasibility and apply penalties using the Big M value
    penalty_m, optimal_value, is_feasible = check_penalty_and_feasibility_minimization(tableau, all_vars, artificial_vars, M, tableau_metadata)

    # Extract the solution from the basic variables
    solution = {}
    for i in range(num_vars):
        if i in tableau_metadata["basis"]:
            row = tableau_metadata["basis"].index(i)
            solution[f"x{i+1}"] = Fraction(tableau[row, -1]).limit_denominator()
        else:
            solution[f"x{i+1}"] = 0

    # Calculate the unpenalized objective value
    unpenalized_objective_value = sum(objective_coeffs[i] * solution[f"x{i+1}"] for i in range(num_vars))

    # Print the objective value without penalties
    print(f"Objective Value (without penalty): Z = {unpenalized_objective_value}")

    # Now handle the penalty due to artificial variables
    if not is_feasible:
        print(f"Warning: Artificial variables are still in the basis, the solution might be infeasible.")
        print(f"Optimal Objective Value: Z = {penalty_m}M + {unpenalized_objective_value}")

    # Print the final solution
    print("Solution:", solution)

    # Check for constraint violations dynamically
    violations = check_constraint_violations(solution, tableau_metadata["constraints"]["coeffs"], tableau_metadata["constraints"]["types"], tableau_metadata["constraints"]["rhs"])
    if violations:
        print_violation_report(violations, all_vars, tableau_metadata["constraints"]["coeffs"])
    else:
        print("All constraints are satisfied.")

elif is_unbounded:
    print("\nThe solution is unbounded.")


# Solve with Pulp to compare
model = LpProblem(name="Minimization_Problem", sense=LpMinimize)
x = {i: LpVariable(name=f"x{i+1}", lowBound=0) for i in range(num_vars)}
model += lpSum(objective_coeffs[i] * x[i] for i in range(num_vars))
for i in range(num_constraints):
    if constraint_types[i] == '<=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) <= b_values[i]
    elif constraint_types[i] == '>=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) >= b_values[i]
    elif constraint_types[i] == '=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) == b_values[i]

model.solve()

print("\nOptimal Solution Reached (Pulp)")
for var in x.values():
    print(f"{var.name}: {var.value()}")
print("Objective Value:", model.objective.value())



Initial Tableau:
╒═══════════════════╤═════════╤══════════╤════════════════╤════════════════╤═══════════╤════════════════╤═══════════╤════════════════╤═══════════╤═════════════════╤═══════════╤═══════════╤═════════════════╤═════════════════╤═══════════╤═════════════════╤══════╤══════╤════════════╤═════════╤══════╤══════╤════════════╤══════╤══════╤════════════╤══════╤══════╤═════════════╤═══════╤═══════╤═══════╤═════════════╤═════════╤═══════╤═══════╤═════════════╤═══════╤════════════╕
│ Constraint Type   │ BASIS   │ x1       │ x2             │ x3             │ x4        │ x5             │ x6        │ x7             │ x8        │ x9              │ x10       │ x11       │ x12             │ x13             │ x14       │ x15             │ s1   │ s2   │ surplus3   │ a3      │ a4   │ s5   │ surplus6   │ a6   │ s7   │ surplus8   │ a8   │ s9   │ surplus10   │ a10   │ s11   │ s12   │ surplus13   │ a13     │ a14   │ s15   │ surplus16   │ a16   │ RHS        │
╞═══════════════════╪═════════╪═════

In [30]:
import numpy as np
from pulp import LpMinimize, LpProblem, LpVariable, lpSum
from fractions import Fraction

# Define the data
MAX_ITERATIONS = 1000
# Define the problem
num_vars = 10
objective_coeffs = [5, 4, 6, 3, 8, 2, 7, 9, 3, 5]
num_constraints = 8
constraint_coeffs = [
    [1, 0, 1, 0, 2, 1, 0, 0, 3, 2],  # Example constraint 1
    [2, 1, 0, 1, 3, 0, 1, 1, 0, 1],  # Example constraint 2
    [0, 1, 2, 0, 1, 3, 0, 2, 1, 1],  # Example constraint 3
    [1, 2, 3, 1, 0, 2, 1, 0, 2, 3],  # Example constraint 4
    [3, 1, 2, 3, 0, 1, 3, 1, 0, 1],  # Example constraint 5
    [0, 2, 1, 3, 1, 0, 2, 3, 1, 0],  # Example constraint 6
    [1, 1, 0, 2, 3, 2, 1, 0, 1, 2],  # Example constraint 7
    [2, 3, 1, 0, 1, 2, 0, 3, 1, 2],  # Example constraint 8
]
constraint_types = ['<=', '<=', '>=', '=', '<=', '>=', '<=', '>=']
b_values = [100, 200, 150, 80, 90, 120, 110, 140]  # Example RHS values

# Create the initial tableau for minimization
tableau, tableau_metadata = create_tableau_only_for_minimization(
    num_vars, objective_coeffs, num_constraints,
    constraint_coeffs, constraint_types, b_values
)

# Add original constraints into tableau_metadata for validation later
tableau_metadata["constraints"] = {
    "coeffs": constraint_coeffs,
    "types": constraint_types,
    "rhs": b_values
}

# Extract metadata
basis = tableau_metadata["basis"]
all_vars = tableau_metadata["all_vars"]
coeffs = tableau_metadata["coeffs"]

# Extract artificial variables from the all_vars list
artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

# Print initial tableau
print("\nInitial Tableau:")
print_tableau_minimization(tableau, all_vars, basis, coeffs, constraint_types)
print("Initial Basis Indices:", basis)
print("Initial Basis Variables and Their Values:")
for row_idx, var_idx in enumerate(basis):
    var_name = all_vars[var_idx]
    value = 1e6 if var_idx in artificial_vars else tableau[row_idx, -1]
    print(f"Variable {var_name} (Index {var_idx}): Value = {value}")

# Perform simplex iterations until an optimal solution is reached or the solution is found to be unbounded
is_optimal = False
is_unbounded = False
iteration_count = 0

# Track previous tableau states to detect cycling
previous_basis_states = []

while not is_optimal and not is_unbounded:
    # Identify the entering column
    entering_column = identify_entering_column_minimization(tableau)
    if entering_column is None:
        is_optimal = True
        break

    # Identify the leaving row
    leaving_row = identify_leaving_row_minimization(tableau, entering_column)
    if leaving_row is None:
        is_unbounded = True
        break

    # Perform pivot operation
    pivot_element = locate_pivot_element_minimization(tableau, entering_column, leaving_row)
    tableau = update_key_row_minimization(tableau, leaving_row, pivot_element)
    tableau = update_non_key_rows_minimization(tableau, entering_column, leaving_row)

    # Update the basis with the new entering variable
    update_basis_with_values(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars)

    # Zero out artificial variables when they leave the basis
    if tableau_metadata["basis"][leaving_row] in artificial_vars:
        tableau[:, tableau_metadata["basis"][leaving_row]] = 0  # Zero out column of leaving artificial variable
        tableau_metadata["coeffs"][tableau_metadata["basis"][leaving_row]] = 0  # Zero out the coefficient

    # Continue with updating the objective row
    update_objective_row_minimization(tableau, tableau_metadata["coeffs"], tableau_metadata["basis"], artificial_vars, all_vars)

    # Print or display the updated tableau for debugging
    print_tableau_minimization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types)

    # Update iteration count to prevent infinite loops
    iteration_count += 1
    if iteration_count > MAX_ITERATIONS:
        print("Max iterations reached, stopping.")
        break

# Define the Big M value (Large penalty)
M = 1e6  # Example value for M

# Perform simplex iterations and find the optimal solution
if is_optimal:
    print("\nOptimal Solution Reached (Custom Simplex Method)")

    # Check for feasibility and apply penalties using the Big M value
    penalty_m, optimal_value, is_feasible = check_penalty_and_feasibility_minimization(tableau, all_vars, artificial_vars, M, tableau_metadata)

    # Extract the solution from the basic variables
    solution = {}
    for i in range(num_vars):
        if i in tableau_metadata["basis"]:
            row = tableau_metadata["basis"].index(i)
            solution[f"x{i+1}"] = Fraction(tableau[row, -1]).limit_denominator()
        else:
            solution[f"x{i+1}"] = 0

    # Calculate the unpenalized objective value
    unpenalized_objective_value = sum(objective_coeffs[i] * solution[f"x{i+1}"] for i in range(num_vars))

    # Print the objective value without penalties
    print(f"Objective Value (without penalty): Z = {unpenalized_objective_value}")

    # Now handle the penalty due to artificial variables
    if not is_feasible:
        print(f"Warning: Artificial variables are still in the basis, the solution might be infeasible.")
        print(f"Optimal Objective Value: Z = {penalty_m}M + {unpenalized_objective_value}")

    # Print the final solution
    print("Solution:", solution)

    # Check for constraint violations dynamically
    violations = check_constraint_violations(solution, tableau_metadata["constraints"]["coeffs"], tableau_metadata["constraints"]["types"], tableau_metadata["constraints"]["rhs"])
    if violations:
        print_violation_report(violations, all_vars, tableau_metadata["constraints"]["coeffs"])
    else:
        print("All constraints are satisfied.")

elif is_unbounded:
    print("\nThe solution is unbounded.")


# Solve with Pulp to compare
model = LpProblem(name="Minimization_Problem", sense=LpMinimize)
x = {i: LpVariable(name=f"x{i+1}", lowBound=0) for i in range(num_vars)}
model += lpSum(objective_coeffs[i] * x[i] for i in range(num_vars))
for i in range(num_constraints):
    if constraint_types[i] == '<=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) <= b_values[i]
    elif constraint_types[i] == '>=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) >= b_values[i]
    elif constraint_types[i] == '=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) == b_values[i]

model.solve()

print("\nOptimal Solution Reached (Pulp)")
for var in x.values():
    print(f"{var.name}: {var.value()}")
print("Objective Value:", model.objective.value())



Initial Tableau:
╒═══════════════════╤═════════╤══════════╤════════════════╤════════════════╤══════════╤════════════════╤══════════╤════════════════╤══════════╤══════════╤══════════╤══════╤══════╤════════════╤═════════╤══════╤══════╤════════════╤══════╤══════╤════════════╤══════╤════════════╕
│ Constraint Type   │ BASIS   │ x1       │ x2             │ x3             │ x4       │ x5             │ x6       │ x7             │ x8       │ x9       │ x10      │ s1   │ s2   │ surplus3   │ a3      │ a4   │ s5   │ surplus6   │ a6   │ s7   │ surplus8   │ a8   │ RHS        │
╞═══════════════════╪═════════╪══════════╪════════════════╪════════════════╪══════════╪════════════════╪══════════╪════════════════╪══════════╪══════════╪══════════╪══════╪══════╪════════════╪═════════╪══════╪══════╪════════════╪══════╪══════╪════════════╪══════╪════════════╡
│ BASIS             │ s1 = 0  │ s2 = 0   │ a3 = 1000000.0 │ a4 = 1000000.0 │ s5 = 0   │ a6 = 1000000.0 │ s7 = 0   │ a8 = 1000000.0 │          │        

In [31]:
import numpy as np
from pulp import LpMinimize, LpProblem, LpVariable, lpSum
from fractions import Fraction

# Define the data
MAX_ITERATIONS = 1000
num_vars = 2
objective_coeffs = [6, 4]
num_constraints = 2
constraint_coeffs = [
    [1, 1],  # Example constraint 1
    [0, 1]   # Example constraint 2
]
constraint_types = ['<=', '>=']
b_values = [5, 8]  # RHS values

# Create the initial tableau for minimization
tableau, tableau_metadata = create_tableau_only_for_minimization(
    num_vars, objective_coeffs, num_constraints,
    constraint_coeffs, constraint_types, b_values
)

# Add original constraints into tableau_metadata for validation later
tableau_metadata["constraints"] = {
    "coeffs": constraint_coeffs,
    "types": constraint_types,
    "rhs": b_values
}

# Extract metadata
basis = tableau_metadata["basis"]
all_vars = tableau_metadata["all_vars"]
coeffs = tableau_metadata["coeffs"]

# Extract artificial variables from the all_vars list
artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

# Print initial tableau
print("\nInitial Tableau:")
print_tableau_minimization(tableau, all_vars, basis, coeffs, constraint_types)
print("Initial Basis Indices:", basis)
print("Initial Basis Variables and Their Values:")
for row_idx, var_idx in enumerate(basis):
    var_name = all_vars[var_idx]
    value = 1e6 if var_idx in artificial_vars else tableau[row_idx, -1]
    print(f"Variable {var_name} (Index {var_idx}): Value = {value}")

# Perform simplex iterations until an optimal solution is reached or the solution is found to be unbounded
is_optimal = False
is_unbounded = False
iteration_count = 0

# Track previous tableau states to detect cycling
previous_basis_states = []

while not is_optimal and not is_unbounded:
    # Identify the entering column
    entering_column = identify_entering_column_minimization(tableau)
    if entering_column is None:
        is_optimal = True
        break

    # Identify the leaving row
    leaving_row = identify_leaving_row_minimization(tableau, entering_column)
    if leaving_row is None:
        is_unbounded = True
        break

    # Perform pivot operation
    pivot_element = locate_pivot_element_minimization(tableau, entering_column, leaving_row)
    tableau = update_key_row_minimization(tableau, leaving_row, pivot_element)
    tableau = update_non_key_rows_minimization(tableau, entering_column, leaving_row)

    # Update the basis with the new entering variable
    update_basis_with_values(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars)

    # Zero out artificial variables when they leave the basis
    if tableau_metadata["basis"][leaving_row] in artificial_vars:
        tableau[:, tableau_metadata["basis"][leaving_row]] = 0  # Zero out column of leaving artificial variable
        tableau_metadata["coeffs"][tableau_metadata["basis"][leaving_row]] = 0  # Zero out the coefficient

    # Continue with updating the objective row
    update_objective_row_minimization(tableau, tableau_metadata["coeffs"], tableau_metadata["basis"], artificial_vars, all_vars)

    # Print or display the updated tableau for debugging
    print_tableau_minimization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types)

    # Update iteration count to prevent infinite loops
    iteration_count += 1
    if iteration_count > MAX_ITERATIONS:
        print("Max iterations reached, stopping.")
        break

# Define the Big M value (Large penalty)
M = 1e6  # Example value for M

# Perform simplex iterations and find the optimal solution
if is_optimal:
    print("\nOptimal Solution Reached (Custom Simplex Method)")

    # Check for feasibility and apply penalties using the Big M value
    penalty_m, optimal_value, is_feasible = check_penalty_and_feasibility_minimization(tableau, all_vars, artificial_vars, M, tableau_metadata)

    # Extract the solution from the basic variables
    solution = {}
    for i in range(num_vars):
        if i in tableau_metadata["basis"]:
            row = tableau_metadata["basis"].index(i)
            solution[f"x{i+1}"] = Fraction(tableau[row, -1]).limit_denominator()
        else:
            solution[f"x{i+1}"] = 0

    # Calculate the unpenalized objective value
    unpenalized_objective_value = sum(objective_coeffs[i] * solution[f"x{i+1}"] for i in range(num_vars))

    # Print the objective value without penalties
    print(f"Objective Value (without penalty): Z = {unpenalized_objective_value}")

    # Now handle the penalty due to artificial variables
    if not is_feasible:
        print(f"Warning: Artificial variables are still in the basis, the solution might be infeasible.")
        print(f"Optimal Objective Value: Z = {penalty_m}M + {unpenalized_objective_value}")

    # Print the final solution
    print("Solution:", solution)

    # Check for constraint violations dynamically
    violations = check_constraint_violations(solution, tableau_metadata["constraints"]["coeffs"], tableau_metadata["constraints"]["types"], tableau_metadata["constraints"]["rhs"])
    if violations:
        print_violation_report(violations, all_vars, tableau_metadata["constraints"]["coeffs"])
    else:
        print("All constraints are satisfied.")

elif is_unbounded:
    print("\nThe solution is unbounded.")


# Solve with Pulp to compare
model = LpProblem(name="Minimization_Problem", sense=LpMinimize)
x = {i: LpVariable(name=f"x{i+1}", lowBound=0) for i in range(num_vars)}
model += lpSum(objective_coeffs[i] * x[i] for i in range(num_vars))
for i in range(num_constraints):
    if constraint_types[i] == '<=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) <= b_values[i]
    elif constraint_types[i] == '>=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) >= b_values[i]
    elif constraint_types[i] == '=':
        model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) == b_values[i]

model.solve()

print("\nOptimal Solution Reached (Pulp)")
for var in x.values():
    print(f"{var.name}: {var.value()}")
print("Objective Value:", model.objective.value())



Initial Tableau:
╒═══════════════════╤═════════╤════════════════╤═════════╤══════╤════════════╤══════╤══════════╕
│ Constraint Type   │ BASIS   │ x1             │ x2      │ s1   │ surplus2   │ a2   │ RHS      │
╞═══════════════════╪═════════╪════════════════╪═════════╪══════╪════════════╪══════╪══════════╡
│ BASIS             │ s1 = 0  │ a2 = 1000000.0 │         │      │            │      │          │
├───────────────────┼─────────┼────────────────┼─────────┼──────┼────────────┼──────┼──────────┤
│ Coeff             │ 6       │ 4              │ 0       │ 0    │ 1000000    │      │          │
├───────────────────┼─────────┼────────────────┼─────────┼──────┼────────────┼──────┼──────────┤
│ <=                │ s1      │ 1              │ 1       │ 1    │ 0          │ 0    │ 5        │
├───────────────────┼─────────┼────────────────┼─────────┼──────┼────────────┼──────┼──────────┤
│ >=                │ a2      │ 0              │ 1       │ 0    │ -1         │ 1    │ 8        │
├───────────